In [ ]:
import sys
sys.path.insert(1, '/work/IFT6010_Story_Tree/src/features/')

from utils_cosine_tf_idf import get_corpus_tf_idf
from utils_cosine_tf_idf import do_cosine_similarity
import utils_cosine_tf_idf as util

import pandas as pd
import pickle
import nltk

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


# Clusters events with community

**Get dataset**

In [ ]:
news_dataset = pd.read_pickle("/work/IFT6010_Story_Tree/data/short_news_dataset_2_with_extractedkeyword.pickle").drop_duplicates(subset=['TEXT'])

In [ ]:
news_dataset

Unnamed: 0                                           KEYWORDS  \
1           1  ['facebook', 'whats', 'world', 'unfolds', 'tam...   
2           2  ['jedi', 'shots', 'rey', 'force', 'wars', 'sta...   
3           3  ['clients', 'art', 'science', 'scent', 'collid...   
4           4  ['akufoaddo', 'tanker', 'incidents', 'dozens',...   
5           5  ['spanish', 'independence', 'regions', 'meets'...   
..        ...                                                ...   
66         66  ['garbage', 'storage', 'cabinet', 'cabinets', ...   
67         67  ['youre', 'answer', 'halloween', 'moments', 'r...   
69         69  ['pizzas', 'pizza', 'hut', 'degrees', 'hotter'...   
70         70  ['race', 'dogs', 'test', 'board', 'drug', 'mus...   
71         71  ['source', '100000', 'secure', 'antifa', 'harn...   

                                              SUMMARY  \
1   Chat with us in Facebook Messenger.\nFind out ...   
2   ESPN's "Monday Night Football" had bears, viki...   
3   Lyn Harris' independent space, Perfumer H , in...   
4   (CNN) A tanker exploded near a gas station in ...   
5   Carles Puigdemont, the President of Catalonia,...   
..                                                ...   
66  1 storage addition is a pullout waste or recyc...   
67  What's the difference between a Halloween cost...   
69  Pizza Hut is introducing a new triple-insulate...   
70  In a statement provided to the Alaska Dispatch...   
71  Mozilla has awarded $100,000 to RiseUp, a secu...   

                                                 TEXT  \
1   Chat with us in Facebook Messenger. Find out w...   
2   ESPN's "Monday Night Football" had bears, viki...   
3   This feature is part of ' Details ,' a new ser...   
4   (CNN) A tanker exploded near a gas station in ...   
5   (CNN) Pro-independence Catalans gathered on th...   
..                                                ...   
66  next\n\nprev next\n\nprev\n\nWaste pullouts ar...   
67  What's the difference between a Halloween cost...   
69  Pizza Hut is introducing a new triple-insulate...   
70  After several doped-up dogs were discovered at...   
71  Mozilla has awarded $100,000 to RiseUp, a secu...   

                                                TITLE        date  \
1                                  Tamagotchi is back  10-06-2017   
2   'Star Wars: The Last Jedi' trailer debuts on '...  10-06-2017   
3   Art and science collide in this one-of-a-kind ...  10-06-2017   
4   Seven killed, dozens injured in Ghana tanker e...  10-06-2017   
5        Catalans' future on line as parliament meets  10-06-2017   
..                                                ...         ...   
66  7 reasons to consider pullout waste and recycl...  10-06-2017   
67  Cosplay or Halloween costume? A cosplay expert...  10-06-2017   
69  Pizza Hut has new pouches that deliver pizzas ...  10-06-2017   
70  Iditarod changes rules after several dogs test...  10-06-2017   
71  Mozilla gave $100,000 to secure email platform...  10-06-2017   

                                   extracted_keywords  
1   [messenger, facebook, chat, find, unfolds, hap...  
2   [monday, trailer, night, rey, jedi, espn, foot...  
3   [details, perfumer, harris', objects, feature,...  
4   [cnn, accra, saturday, ghana, people, official...  
5   [spain, catalan, independence, puigdemont, bar...  
..                                                ...  
66  [waste, pullout, bins, garbage, prev, chopping...  
67  [comic, halloween, voltron, orsini, asuncion, ...  
69  [pouch, pizzas, allen, parka, crisp, oct, pdt,...  
70  [dogs, race, mushers, trail, positive, tested,...  
71  [riseup, mozilla, source, open, platform, face...  

[827 rows x 7 columns]

**Get communities**

In [ ]:
temp_defaultdict_communities = pickle.load(open("extracted_communities.pickle",'rb'))
dict_communities = {}
for i,v in temp_defaultdict_communities.items():
    if len(v)==1:
        dict_communities[i] = v[0]

In [ ]:
keywords_clusters = pd.DataFrame(dict_communities.items())
keywords_clusters.columns = ['keyword', 'cluster']

**Get tfidf vector for keywords**

In [ ]:
#arg 1 = dataframe source
#arg 2 = colomne d'ou le texte provient (je l'ai mis en argument parce que je ne connais pas la structure des autres dataframe)
##arg 3 = ngram a considerer... possible solution pour les keywords a n mots (n>1)

dataset_tf_idf, dict_weights = get_corpus_tf_idf(news_dataset,'TEXT',ngram=1)
dataset_tf_idf = dataset_tf_idf.drop_duplicates(subset=['TEXT'])

In [ ]:
dataset_tf_idf

Unnamed: 0                                           KEYWORDS  \
1           1  ['facebook', 'whats', 'world', 'unfolds', 'tam...   
2           2  ['jedi', 'shots', 'rey', 'force', 'wars', 'sta...   
3           3  ['clients', 'art', 'science', 'scent', 'collid...   
4           4  ['akufoaddo', 'tanker', 'incidents', 'dozens',...   
5           5  ['spanish', 'independence', 'regions', 'meets'...   
..        ...                                                ...   
66         66  ['garbage', 'storage', 'cabinet', 'cabinets', ...   
67         67  ['youre', 'answer', 'halloween', 'moments', 'r...   
69         69  ['pizzas', 'pizza', 'hut', 'degrees', 'hotter'...   
70         70  ['race', 'dogs', 'test', 'board', 'drug', 'mus...   
71         71  ['source', '100000', 'secure', 'antifa', 'harn...   

                                              SUMMARY  \
1   Chat with us in Facebook Messenger.\nFind out ...   
2   ESPN's "Monday Night Football" had bears, viki...   
3   Lyn Harris' independent space, Perfumer H , in...   
4   (CNN) A tanker exploded near a gas station in ...   
5   Carles Puigdemont, the President of Catalonia,...   
..                                                ...   
66  1 storage addition is a pullout waste or recyc...   
67  What's the difference between a Halloween cost...   
69  Pizza Hut is introducing a new triple-insulate...   
70  In a statement provided to the Alaska Dispatch...   
71  Mozilla has awarded $100,000 to RiseUp, a secu...   

                                                 TEXT  \
1   Chat with us in Facebook Messenger. Find out w...   
2   ESPN's "Monday Night Football" had bears, viki...   
3   This feature is part of ' Details ,' a new ser...   
4   (CNN) A tanker exploded near a gas station in ...   
5   (CNN) Pro-independence Catalans gathered on th...   
..                                                ...   
66  next\n\nprev next\n\nprev\n\nWaste pullouts ar...   
67  What's the difference between a Halloween cost...   
69  Pizza Hut is introducing a new triple-insulate...   
70  After several doped-up dogs were discovered at...   
71  Mozilla has awarded $100,000 to RiseUp, a secu...   

                                                TITLE        date  \
1                                  Tamagotchi is back  10-06-2017   
2   'Star Wars: The Last Jedi' trailer debuts on '...  10-06-2017   
3   Art and science collide in this one-of-a-kind ...  10-06-2017   
4   Seven killed, dozens injured in Ghana tanker e...  10-06-2017   
5        Catalans' future on line as parliament meets  10-06-2017   
..                                                ...         ...   
66  7 reasons to consider pullout waste and recycl...  10-06-2017   
67  Cosplay or Halloween costume? A cosplay expert...  10-06-2017   
69  Pizza Hut has new pouches that deliver pizzas ...  10-06-2017   
70  Iditarod changes rules after several dogs test...  10-06-2017   
71  Mozilla gave $100,000 to secure email platform...  10-06-2017   

                                   extracted_keywords  \
1   [messenger, facebook, chat, find, unfolds, hap...   
2   [monday, trailer, night, rey, jedi, espn, foot...   
3   [details, perfumer, harris', objects, feature,...   
4   [cnn, accra, saturday, ghana, people, official...   
5   [spain, catalan, independence, puigdemont, bar...   
..                                                ...   
66  [waste, pullout, bins, garbage, prev, chopping...   
67  [comic, halloween, voltron, orsini, asuncion, ...   
69  [pouch, pizzas, allen, parka, crisp, oct, pdt,...   
70  [dogs, race, mushers, trail, positive, tested,...   
71  [riseup, mozilla, source, open, platform, face...   

                                   PREPROCESSING_TEXT  \
1   chat us facebook messenger find 's happening w...   
2   espn 's monday night football '' bears vikings...   
3   feature part details new series captures creat...   
4   cnn tanker exploded near gas station accra sat...   
5   cnn proindepe

In [ ]:
from nltk.stem import PorterStemmer
porter = PorterStemmer()
lemmatizer = porter.stem

dict_weights_lemmatized = {}
for i,v in dict_weights.items():
    dict_weights_lemmatized[lemmatizer(i)] = v

In [ ]:
do_cosine_similarity(dataset_tf_idf.iloc[0]['VECTOR'],dataset_tf_idf.iloc[2]['VECTOR'])

0.25776752962351324

**Assign document to community**

In [ ]:
# for the cluster, we assume they are in a dataframe
def prepare_cluster_vector(dataframe, dict_weights):
    all_cluster = dataframe['cluster'].unique()

    all_cluster_dict = {}

    for cluster in all_cluster:
        cluster_dict ={}
        all_keyword=list(dataframe[dataframe["cluster"] == cluster]['keyword'])
        all_keyword=' '.join(all_keyword)

        # We will have more keywords than 
        tokens = nltk.word_tokenize(all_keyword)
        
        #!!!!DEAL with keyword with multiple word ... some keyword are not int the dictionary of all weights
        for token in tokens:
            if token in dict_weights:
                cluster_dict[token]=dict_weights[token]
            else:
                cluster_dict[token]=0

        # print(cluster_dict)
        all_cluster_dict[cluster]=cluster_dict
        
    return all_cluster_dict

In [ ]:
clusters_vector = prepare_cluster_vector(keywords_clusters, dict_weights_lemmatized)

In [ ]:
total_len=0
for i in range(len(clusters_vector)):
    
    total_len += len(clusters_vector[i])
print(total_len)

761


In [ ]:
do_cosine_similarity(dataset_tf_idf.iloc[2]['VECTOR'],clusters_vector[0])

0.017989580910794833

In [ ]:
def set_document_topic(document_vector, all_cluster_vector):
    max_cluster_name=''
    max_cluster_value=0
    for cluster in all_cluster_vector:
        cluster_value= do_cosine_similarity(document_vector,clusters_vector[cluster])
        # print(cluster_value)

        if (max_cluster_value<cluster_value):
            max_cluster_value=cluster_value
            max_cluster_name=cluster
    
    # print(max_cluster_name)
    # print(max_cluster_value)
    return max_cluster_name

In [ ]:
dataset_tf_idf['TOPIC']=dataset_tf_idf['VECTOR'].apply(set_document_topic,all_cluster_vector=clusters_vector)

In [ ]:
dataset_tf_idf['TOPIC'].value_counts()

0    488
1    270
2     36
3     22
5      5
       4
4      2
Name: TOPIC, dtype: int64

In [ ]:
dataset_tf_idf[dataset_tf_idf['TOPIC'] == 1]

Unnamed: 0                                           KEYWORDS  \
1           1  ['facebook', 'whats', 'world', 'unfolds', 'tam...   
2           2  ['jedi', 'shots', 'rey', 'force', 'wars', 'sta...   
8           8  ['look', 'response', 'force', 'trump', 'tour',...   
9           9  ['okunoin', 'tohoku', 'japan', 'risshakuji', '...   
19         19  ['according', 'boundaries', 'generations', 'ac...   
..        ...                                                ...   
61         61  ['america', 'peter', 'tend', 'prosperous', 'ur...   
64         64  ['launch', 'hellcat', 'challenger', 'car', 'tr...   
67         67  ['youre', 'answer', 'halloween', 'moments', 'r...   
69         69  ['pizzas', 'pizza', 'hut', 'degrees', 'hotter'...   
71         71  ['source', '100000', 'secure', 'antifa', 'harn...   

                                              SUMMARY  \
1   Chat with us in Facebook Messenger.\nFind out ...   
2   ESPN's "Monday Night Football" had bears, viki...   
8   (CNN) Finally lumbering into a devastated Puer...   
9   (CNN) — Upon hearing I would have to climb 1,0...   
19  "The only generation we do define is Baby Boom...   
..                                                ...   
61  However, the Democrats often behave as if they...   
64  There’s no better place to test drive the Dodg...   
67  What's the difference between a Halloween cost...   
69  Pizza Hut is introducing a new triple-insulate...   
71  Mozilla has awarded $100,000 to RiseUp, a secu...   

                                                 TEXT  \
1   Chat with us in Facebook Messenger. Find out w...   
2   ESPN's "Monday Night Football" had bears, viki...   
8   Michael D'Antonio is the author of the book " ...   
9   \n\n\n\nThis article was first published in Ju...   
19  We can all agree that Millennials are the wors...   
..                                                ...   
61  Editor's note: The following column originally...   
64  There’s no better place to test drive the Dodg...   
67  What's the difference between a Halloween cost...   
69  Pizza Hut is introducing a new triple-insulate...   
71  Mozilla has awarded $100,000 to RiseUp, a secu...   

                                                TITLE        date  \
1                                  Tamagotchi is back  10-06-2017   
2   'Star Wars: The Last Jedi' trailer debuts on '...  10-06-2017   
8   Trump in Puerto Rico: A narcissist's tour de f...  10-06-2017   
9   Yamadera Risshakuji in Tohoku: 1,015 steps to ...  10-06-2017   
19  Here Is When Each Generation Begins and Ends, ...  10-06-2017   
..                                                ...         ...   
61  Peter Morici: Trump’s immigration proposals wo...  10-06-2017   
64         2018 Dodge Challenger SRT Demon test drive  10-06-2017   
67  Cosplay or Halloween costume? A cosplay expert...  10-06-2017   
69  Pizza Hut has new pouches that deliver pizzas ...  10-06-2017   
71  Mozilla gave $100,000 to secure email platform...  10-06-2017   

                                   extracted_keywords  \
1   [messenger, facebook, chat, find, unfolds, hap...   
2   [monday, trailer, night, rey, jedi, espn, foot...   
8   [trump, puerto, reality, success, press, pursu...   
9   [temple, cnn, risshakuji, japan, hall, june, b...   
19  [millennials, slate, diprete, article, worst, ...   
..                                                ...   
61  [trump, baltimore, immigrants, growth, border,...   
64  [challenger, srt, launch, control, dodge, engi...   
67  [comic, halloween, voltron, orsini, asuncion, ...   
69  [pouch, pizzas, allen, parka, crisp, oct, pdt,...   
71  [riseup, mozilla, source, open, platform, face...   

                                   PREPROCESSING_TEXT  \
1   chat us facebook messenger find 's happening w...   
2   espn 's monday night football '' bears vikings...   
8   michael d'antonio author book never enough don...   
9   article first published june editor 's note cn...   
19  agree millenn

# Regroup document that talk about the same event

In [ ]:
!pip install gensim

     |████████████████████████████████| 23.9 MB 31.7 MB/s 
You should consider upgrading via the '/root/venv/bin/python -m pip install --upgrade pip' command.


In [ ]:
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
import re
from scipy import spatial

/root/venv/lib/python3.7/site-packages/gensim/similarities/__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)


In [ ]:
documents = [TaggedDocument(doc["TEXT"], [i]) for i, doc in news_dataset.iterrows()]
model = Doc2Vec(documents, vector_size=150, window=3, min_count=1, workers=4)

In [ ]:
vector_document = []

for i in range(len(news_dataset)):
    vector_document.append( model.infer_vector(re.split('"|\n| ', news_dataset.iloc[1]["TEXT"])) )

In [ ]:
news_dataset["text_doc2vec"] = vector_document

In [ ]:
# distance of 0.0 means it's the same
spatial.distance.cosine(news_dataset.iloc[200]["text_doc2vec"], news_dataset.iloc[200]["text_doc2vec"])

0.0

In [ ]:
dict_ = {}

for i in range(len(news_dataset)):
    for j in range(len(news_dataset)):
        dict_[f"{i}_{j}"] = spatial.distance.cosine(news_dataset.iloc[i]["text_doc2vec"], news_dataset.iloc[j]["text_doc2vec"])

In [ ]:
for i,v in dict_.items():
    index = i.split("_")
    if(index[0] != index[1]):
        if v<0.008:
            print(i)

30_551
38_309
309_38
423_724
551_30
724_423


In [ ]:
dict_tfdif = {}

for i in range(len(news_dataset)):
    for j in range(len(news_dataset)):
        dict_tfdif[f"{i}_{j}"] = do_cosine_similarity(dataset_tf_idf.iloc[i]["VECTOR"], dataset_tf_idf.iloc[j]["VECTOR"])

In [ ]:
dataset_tf_idf = dataset_tf_idf.drop_duplicates(subset=['TITLE'])

for i,v in dict_tfdif.items():
    index = i.split("_")
    if(index[0] != index[1]):
        if 0.8<v<0.9:
            print(dataset_tf_idf.iloc[int(index[0])]["KEYWORDS"])
            print(dataset_tf_idf.iloc[int(index[1])]["KEYWORDS"])
            print("--------------------------------------------------------------------------------------------------------")

['hide', 'victims', 'california', 'burns', '31photos', 'wildfires', 'caption', 'help', 'blaze', 'santa', 'rosa', 'napa']
['unhappy', 'zelizer', 'secretary', 'state', 'trump', 'rex', 'tillerson', 'administration', 'president', 'trumps', 'quit', 'white']
--------------------------------------------------------------------------------------------------------
['harvey', 'changedby', 'continuing', 'hosts', 'terms', 'service', 'weigh', 'site', 'policy', 'weinstein', 'late', 'night', 'privacy', 'agreeing']
['cookies', 'revised', 'continuing', 'information', 'terms', 'service', 'havana', 'browse', 'site', 'privacy', 'policy', 'cuba', 'photos']
--------------------------------------------------------------------------------------------------------
['cookies', 'revised', 'continuing', 'information', 'terms', 'service', 'havana', 'browse', 'site', 'privacy', 'policy', 'cuba', 'photos']
['harvey', 'changedby', 'continuing', 'hosts', 'terms', 'service', 'weigh', 'site', 'policy', 'weinstein', 'late

In [ ]:
350_337
print()

In [ ]:
dataset_tf_idf[dataset_tf_idf["TITLE"] == "Transcripts"]

Unnamed: 0                                           KEYWORDS  \
103        103  ['page', 'updated', 'specific', 'transcripts',...   
113        113  ['page', 'updated', 'specific', 'transcripts',...   
366        366  ['page', 'updated', 'specific', 'transcripts',...   
381        381  ['page', 'updated', 'specific', 'transcripts',...   
469        469  ['page', 'updated', 'specific', 'transcripts',...   
497        497  ['page', 'updated', 'specific', 'transcripts',...   
554        554  ['page', 'updated', 'specific', 'transcripts',...   
585        585  ['page', 'updated', 'specific', 'transcripts',...   
630        630  ['page', 'updated', 'specific', 'transcripts',...   
914        914  ['page', 'updated', 'specific', 'transcripts',...   

                                               SUMMARY  \
103  Return to Transcripts main pageCNN Transcripts...   
113  Return to Transcripts main pageCNN Transcripts...   
366  Return to Transcripts main pageCNN Transcripts...   
381  Return to Transcripts main pageCNN Transcripts...   
469  Return to Transcripts main pageCNN Transcripts...   
497  Return to Transcripts main pageCNN Transcripts...   
554  Return to Transcripts main pageCNN Transcripts...   
585  Return to Transcripts main pageCNN Transcripts...   
630  Return to Transcripts main pageCNN Transcripts...   
914  Return to Transcripts main pageCNN Transcripts...   

                                                  TEXT        TITLE  \
103  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
113  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
366  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
381  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
469  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
497  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
554  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
585  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
630  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   
914  \n\n\n\nReturn to Transcripts main page\n\nCNN...  Transcripts   

           date                                 extracted_keywords  \
103  10-06-2017  [note, october, cnn, return, continually, segm...   
113  10-06-2017  [note, october, cnn, return, continually, segm...   
366  10-06-2017  [note, october, cnn, return, continually, segm...   
381  10-06-2017  [note, october, cnn, return, continually, segm...   
469  10-06-2017  [note, october, cnn, return, continually, segm...   
497  10-06-2017  [note, october, cnn, return, continually, segm...   
554  10-06-2017  [note, october, cnn, return, continually, segm...   
585  10-06-2017  [note, october, cnn, return, continually, segm...   
630  10-06-2017  [note, october, cnn, return, continually, segm...   
914  10-06-2017  [note, october, cnn, return, continually, segm...   

                                    PREPROCESSING_TEXT  \
103  return transcripts main page cnn transcripts o...   
113  return transcripts main page cnn transcripts o...   
366  return transcripts main page cnn transcripts o...   
381  return transcripts main page cnn transcripts o...   
469  return transcripts main page cnn transcripts o...   
497  return transcripts main page cnn transcripts o...   
554  return transcripts main page cnn transcripts o...   
585  return transcripts main page cnn transcripts o...   
630  return transcripts main page cnn transcripts o...   
914  return transcripts main page cnn transcripts o...   

                                                VECTOR TOPIC  
103  {'return': 0.0037393434301340855, 'transcripts...     3  
113  {'return': 0.0037393434301340855, 'transcripts...     3  
366  {'return': 0.0037393434301340855, 'transcripts...     3  
381  {'return': 0.0037393434301340855, 'transcripts...     3  
469  {'return': 0.0037393434301340855, 'transcripts...     3  
497  {'return': 0.00373934343013408

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=902703f2-430f-48f3-ba3f-6c2fee66cf11' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>